In [36]:
from sklearn import preprocessing as pp
import numpy as np
from music21 import converter, instrument, note, chord, stream
import glob
import pickle
from keras.utils import np_utils
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.layers import Activation
from keras.layers import BatchNormalization as BatchNorm
from keras.layers import Lambda
from keras.callbacks import ModelCheckpoint
from keras.models import load_model
from numpy.random import multinomial as randm

# Current Counts = Current Counts + Note Length % 16 ?

def buildNotes():
    
    print("In buildNotes()")
    
    notes = []
    noteLengths = []
    
    for file in glob.glob("Music/*.mid"):
        
        try:
            midi = converter.parse(file)    
            
        except:
            print("MIDI file %s failed to parse" % file)
            continue
            
        print("Parsing %s" % file)
        notesToParse = None
        
        try: # file has instrument parts
            s2 = instrument.partitionByInstrument(midi)
            notesToParse = s2.parts[0].recurse()
            print("Instrument Parts %d" % len(s2.parts))
            
        except: # file has notes in a flat structure
            notesToParse = midi.flat.notes
            
        # For each note in notesToParse (a stream of notes)
            
        for element in notesToParse:
            
            # Interesting parameters of notes that we may want to look at here.
            
            if isinstance(element, note.Note):
                notes.append(str(element.pitch))
                noteLengths.append(str(float(element.quarterLength)))
                
            elif isinstance(element, chord.Chord):
                notes.append('.'.join(str(n) for n in element.normalOrder))
                noteLengths.append(str(float(element.quarterLength)))

    pickle.dump(notes, open('notes.p', 'wb'))
    pickle.dump(noteLengths, open('noteLengths.p', 'wb'))

    return notes, noteLengths

def prepareSeq(notes, noteLengths):

    seqLength = 16 # S Sequence Length
    inputSize = len(notes) - seqLength # N Samples
    categories = 2 # C Categories
    
    # Yields N x S x C array
    
    pitchSet = sorted(set(notes))
    npitch = len(pitchSet)
    noteToInt = dict((note, number) for number, note in enumerate(pitchSet))
    
    lengthSet = sorted(set(noteLengths))
    nlengths = len(lengthSet)
    lengthToInt = dict((length, number) for number, length in enumerate(lengthSet))
    
    # We only have 2 dimensions at the moment, pitch and length
    # noteIn - a collection of categorical arrays, each row is one category
    # noteOut - the integer which converts to the index of that category's respective
    # one hot encoding.  These categorical one hot encodings are later concatenated
    # columnwise to form a multi hot encoding.

    # This representation is a C x N x S array
    
    noteIn = [
        [],
        []
    ]
    
    noteOut = [
        [],
        []
    ]

    # Mapping of i:i+seqLength notes to note i + seqLength
    
    # X[0] sequence_in : [seqLength]
    # X[1] length_in : [seqLength]
    
    # Y[0] sequence_out : 1
    # Y[1] length_out : 1
    
    for i in range(0, inputSize, 1):
        
        sequence_in = notes[i:i + seqLength]
        sequence_out = notes[i + seqLength]
        
        length_in = noteLengths[i:i + seqLength]
        length_out = noteLengths[i + seqLength]
        
        noteIn[0].append([noteToInt[char] for char in sequence_in])
        noteIn[1].append([lengthToInt[char] for char in length_in])
        
        noteOut[0].append(noteToInt[sequence_out])
        noteOut[1].append(lengthToInt[length_out])
        
    # npatterns = len(noteIn) (inputSize)

    # reshape the input into a format compatible with LSTM layers
    # noteIn = np.reshape(noteIn, (inputSize, seqLength, 1))
    
    noteIn = np.array(noteIn, dtype=float)
    noteOut = np.array(noteOut, dtype=float)
    
    # normalize input
    noteIn[0] = noteIn[0] / float(npitch)
    noteIn[1] = noteIn[1] / float(nlengths)
    
    print("noteIn shape:")
    print(noteIn.shape)
    print("noteOut shape:")
    print(noteOut.shape)
    print(noteIn)
    
    catNote = np_utils.to_categorical(noteOut[0])
    catLength = np_utils.to_categorical(noteOut[1])
    
    # Concatenate the input arrays row wise
    # Concatenate the categorical arrays along axis 1 (columnwise)
    
    print("noteIn:")
    print(noteIn)
    
    # Convert from C x N x S to N x S x C
    
    reshape = []
    for N in range(inputSize):
        for S in range(seqLength):
            for C in range(categories):
                reshape.append(noteIn[C][N][S])
    
    dout = np.concatenate((catNote, catLength), 1)
    din = np.reshape(reshape, (inputSize, seqLength, categories))
    
    print("din shape:")
    print(din.shape)
    print("dout shape:")
    print(dout.shape)
    print("din:")
    print(din)
    
    print(len(catNote[0]))
    print(len(catLength[0]))
    
    print(din[0][0][0])
    print(din[0][0][1])

    return (din, dout)


In [37]:
# print(np.arange(10).reshape(5,2).T.flatten())
notes, noteLengths = buildNotes()
noteIn, noteOut = prepareSeq(notes, noteLengths)
print(noteIn.shape)
print(noteOut.shape)

In buildNotes()
Parsing Music\Fugue1.mid
Parsing Music\Fugue10.mid
Parsing Music\Fugue11.mid
MIDI file Music\Fugue12.mid failed to parse
Parsing Music\Fugue13.mid
Parsing Music\Fugue14.mid
Parsing Music\Fugue15.mid
Parsing Music\Fugue16.mid
Parsing Music\Fugue17.mid
Parsing Music\Fugue18.mid
MIDI file Music\Fugue19.mid failed to parse
Parsing Music\Fugue2.mid
Parsing Music\Fugue20.mid
Parsing Music\Fugue21.mid
Parsing Music\Fugue22.mid
Parsing Music\Fugue23.mid
Parsing Music\Fugue24.mid
Parsing Music\Fugue3.mid
Parsing Music\Fugue4.mid
Parsing Music\Fugue5.mid
MIDI file Music\Fugue6.mid failed to parse
Parsing Music\Fugue7.mid
Parsing Music\Fugue8.mid
Parsing Music\Fugue9.mid
Instrument Parts 1
noteIn shape:
(2, 22362, 16)
noteOut shape:
(2, 22362)
[[[0.60759494 0.67088608 0.7721519  ... 0.7721519  0.87341772 0.97468354]
  [0.67088608 0.7721519  0.87341772 ... 0.87341772 0.97468354 0.7721519 ]
  [0.7721519  0.87341772 0.97468354 ... 0.97468354 0.7721519  0.67088608]
  ...
  [0.55696203

In [38]:
def createNet(noteIn, nvocab):

    print("In createNet()")
    
    print(noteIn.shape)
    
    model = Sequential()
    model.add(LSTM(
        512,
        input_shape=(noteIn.shape[1], noteIn.shape[2]),
        recurrent_dropout=0.3,
        return_sequences=True
    ))
    
    # Chris's code
    model.add(LSTM(
        512,
        input_shape=(noteIn.shape[1], noteIn.shape[2]),
        recurrent_dropout=0.3,
        return_sequences=False
    ))
    
    model.add(BatchNorm())
    model.add(Dropout(0.3))
    model.add(Dense(256))
    model.add(Activation(activation='relu'))
    model.add(BatchNorm())
    model.add(Dropout(0.3))
    
    #model.add(Flatten())
    
    model.add(Dense(nvocab))
    # model.add(Lambda(lambda x: x / 0.6))
    model.add(Activation(activation='sigmoid'))

    model.compile(
            loss='categorical_crossentropy',
            optimizer='adam',
            metrics=['accuracy']
        )
    
    return model

def trainNet(_epochs=1):
    """ Train a Neural Network to generate music """
    notes, noteLengths = buildNotes()

    nvocab = len(set(notes)) + len(set(noteLengths))
    
    noteIn, noteOut = prepareSeq(notes, noteLengths)
    
    model = createNet(noteIn, nvocab)
 
    checkpoint = ModelCheckpoint(
        "weights2-improvement-{epoch:02d}-{loss:.4f}-bigger.hdf5",
        monitor='loss',
        verbose=0,
        save_best_only=True,
        mode='min'
    )

    callbacks_list = [checkpoint]

    # Your line of code here
    model.fit(noteIn, noteOut, batch_size=1024, epochs=_epochs, verbose=1, callbacks=callbacks_list)
    


In [6]:
trainNet(10)

In buildNotes()
Parsing Music\Fugue1.mid
Parsing Music\Fugue10.mid
Parsing Music\Fugue11.mid
MIDI file Music\Fugue12.mid failed to parse
Parsing Music\Fugue13.mid
Parsing Music\Fugue14.mid
Parsing Music\Fugue15.mid
Parsing Music\Fugue16.mid
Parsing Music\Fugue17.mid
Parsing Music\Fugue18.mid
MIDI file Music\Fugue19.mid failed to parse
Parsing Music\Fugue2.mid
Parsing Music\Fugue20.mid
Parsing Music\Fugue21.mid
Parsing Music\Fugue22.mid
Parsing Music\Fugue23.mid
Parsing Music\Fugue24.mid
Parsing Music\Fugue3.mid
Parsing Music\Fugue4.mid
Parsing Music\Fugue5.mid
MIDI file Music\Fugue6.mid failed to parse
Parsing Music\Fugue7.mid
Parsing Music\Fugue8.mid
Parsing Music\Fugue9.mid
Instrument Parts 1
noteIn shape:
(2, 22362, 16)
noteOut shape:
(2, 22362)
[[[0.60759494 0.67088608 0.7721519  ... 0.7721519  0.87341772 0.97468354]
  [0.67088608 0.7721519  0.87341772 ... 0.87341772 0.97468354 0.7721519 ]
  [0.7721519  0.87341772 0.97468354 ... 0.97468354 0.7721519  0.67088608]
  ...
  [0.55696203

In [78]:
def generate(model):
    
    print("In Generate")
    
    notes = pickle.load(open('notes.p', 'rb'))
    noteLengths = pickle.load(open('noteLengths.p', 'rb'))

    pitchSet = sorted(set(notes))
    lengthSet = sorted(set(noteLengths))
    
    # 1. Call to prepareSeqPred
    
    noteIn = prepareSeqPred(notes, noteLengths) 
    
    # print("Model Loaded")
    
    # 2. Call to genNotes
    
    predOut = genNotes(model, noteIn, pitchSet, lengthSet)
    
    # 3. Call to createMidi
    createMidi(predOut)

# 1.
    
def prepareSeqPred(notes, noteLengths):
    
    print("In Prepare Sequences Prediction")
    
    seqLength = 16
    inputSize = len(notes) - seqLength
    categories = 2
    
    pitchSet = sorted(set(notes))
    npitch = len(pitchSet)
    noteToInt = dict((note, number) for number, note in enumerate(pitchSet))
    
    lengthSet = sorted(set(noteLengths))
    nlengths = len(lengthSet)
    lengthToInt = dict((length, number) for number, length in enumerate(lengthSet))
    
    print("lengthToInt: %s" % lengthToInt)
    
    noteIn = [
        [],
        []
    ]
    
    noteOut = [
        [],
        []
    ]
    
    for i in range(0, inputSize, 1):
        
        sequence_in = notes[i:i + seqLength]
        length_in = noteLengths[i:i + seqLength]
        
        sequence_out = notes[i + seqLength]
        length_out = noteLengths[i + seqLength]
        
        noteIn[0].append([noteToInt[char] for char in sequence_in])
        noteOut[0].append(noteToInt[sequence_out])
        
        noteIn[1].append([lengthToInt[char] for char in length_in])
        noteOut[1].append(lengthToInt[length_out])
        
    noteIn = np.array(noteIn, dtype=float)
    noteOut = np.array(noteOut, dtype=float)
    
    # normalize input
    noteIn[0] = noteIn[0] / float(npitch)
    noteIn[1] = noteIn[1] / float(nlengths)
        
    reshape = []
    for N in range(inputSize):
        for S in range(seqLength):
            for C in range(categories):
                reshape.append(noteIn[C][N][S])
    
    din = np.reshape(reshape, (inputSize, seqLength, categories))
        
    print("din shape:")
    print(din.shape)
    print("din:")
    print(din)

    return din

# 2.

def inKey(note, semiScale, chromaDict):
    
    print("Testing %s" % note)
    pitch = ''.join([i for i in note if not i.isdigit()])
    print("pitch %s" % pitch)
    
    # Except chords for now
    if len(pitch) == 0 or pitch[0] == '.':
        return True
    
    return chromaDict[pitch] in semiScale

def getNearest(number, semiScale, chromaDict, intToNote):

    low = number - 1
    high = number + 1
    
    while(True):
        if low in intToNote.keys():
            if(inKey(intToNote[low], semiScale, chromaDict)):
                return intToNote[low]
            low -= 1
        elif high in intToNote.keys():
            if(inKey(intToNote[high], semiScale, chromaDict)):
                return intToNote[high]
            high += 1
        else:
            break
            
    return None
    

def genNotes(model, noteIn, pitchSet, lengthSet):
    
    # Specify a key as a list of semitones in the scale:
    chromaSharp = ['C','C#','D','D#','E','F','F#','G','G#','A','A#','B']
    chromaFlat =  ['C','D-','D','E-','E','F','G-','G','A-','A','B-','B']
    
    chromaDict = {}
    for semitone, note in enumerate(chromaSharp):
        chromaDict[note] = semitone
    for semitone, note in enumerate(chromaFlat):
        chromaDict[note] = semitone
    
    print("chromaDict")
    print(chromaDict)
    
    # semiScale specifies our key filter
    
    semiScale = [0,2,4,5,7,9,11] # C Major
        
    # Hook for Key Filter goes here, map each out of key note to nearest in key note available.
    
    intToNote = dict((number, note) for number, note in enumerate(pitchSet))
    intToLength = dict((number, length) for number, length in enumerate(lengthSet))
    
    convNote = intToNote.copy()
    
    for number in convNote:
        print("On note: # %s %s" % (number, convNote[number]))
        if inKey(convNote[number], semiScale, chromaDict):
            print("inKey")
        else:
            convNote[number] = getNearest(number, semiScale, chromaDict, convNote)
            print("Note adjusted to: %s" % convNote[number])
            
    print("In genNotes()")
    
    """ Generate notes from the neural network based on a sequence of notes """
    # Starts the melody by picking a random sequence from the input as a starting point
    
    inputSize = len(noteIn)
        
    start = np.random.randint(0, inputSize - 1)
    pattern = noteIn[start] # Remember that it is an N x S x C
    
    print("pattern %s" % pattern)
        
    seqLength = len(pattern)
    categories = 2
    
    print("seqLength: %d" % seqLength)

    npitches = len(pitchSet)
    nlengths = len(lengthSet)
    
    print("npitches %d nlengths %d" % (npitches, nlengths))
    
    predOut = []
    
    print("In genNotes(): noteIn[start] = %s" % pattern)
    print("inputSize: %d" % inputSize)
    print("categories: %d" % categories)
    
    print("pitchSet %s" % pitchSet)
    print("lengthSet %s" % lengthSet)

    for i in range(1000):
        
        # Reshape a single sample into 1 x S x C array
        
        prediction_input = np.reshape(pattern, (1, seqLength, categories))
        
        print("prediction_input:")
        print(prediction_input)
        
        ### Complete the line below
        prediction = model.predict(np.array(prediction_input))
        print(len(prediction[0]))       
        print("prediction: %s" % prediction[0])
        print("prediction length: %d" % len(prediction[0]))
        
        predPitch = prediction[0][:npitches].astype('float64')
        predLength = prediction[0][npitches:].astype('float64')
        
        print("Before")
        print(predPitch)
        print(predLength)
        
        #predPitch /= sumNote
        #predLength /= sumLength
        
        print("sumNote %f sumLength %f" % (predPitch.sum(), predLength.sum()))
        
        predPitch /= predPitch.sum()
        predLength /= predLength.sum()
        
        print("After")
        print(predPitch)
        print(predLength)
        
        print("sumNote %f sumLength %f" % (predPitch.sum(), predLength.sum()))
        
        array = randm(1, predPitch)
        print("array predPitch: %s" % array)
        indexPitch = np.argmax(array)
        
        array = randm(1, predLength)
        print("array predLength: %s" % array)
        indexLength = np.argmax(array)
        
        # return tuple pitch, length
        noteData = convNote[indexPitch]
        lengthData = intToLength[indexLength]
        
        result = np.array([noteData, lengthData])
        predOut.append(result)
        
        print("result %s" % result)
        
        append = np.reshape(np.array([indexPitch/float(npitches), indexLength/float(nlengths)]), (1,2))
        pattern = np.concatenate((pattern, append))
        
        print("pattern: %s" % pattern)
        
        pattern = pattern[1:len(pattern)]
        
    print(predOut)

    return predOut

# 3.

def createMidi(predOut):
    
    print("In createMidi()")

    itempo = 0.25
    offset = 0
    
    output_notes = []
    
    for pattern in predOut:
        if ('.' in pattern[0]) or pattern[0].isdigit():
            notes_in_chord = pattern[0].split('.')
            notes = []
            for current_note in notes_in_chord:
                new_note = note.Note(int(current_note))
                new_note.storedInstrument = instrument.Piano()
                if pattern[1] != '0.0':
                    new_note.quarterLength = float(pattern[1]) # Assign duration
                notes.append(new_note)
            new_chord = chord.Chord(notes)
            new_chord.offset = offset
            output_notes.append(new_chord)
        else:
            new_note = note.Note(pattern[0])
            new_note.offset = offset
            new_note.storedInstrument = instrument.Piano()
            if pattern[1] != '0.0':
                new_note.quarterLength = float(pattern[1]) # Assign duration
            output_notes.append(new_note)
        #offset += itempo
        offset += float(patter[1]/4)
        print("Pattern %d: pitch %s duration %s" % (offset, pattern[0], pattern[1]))
    midi_stream = stream.Stream(output_notes)
    midi_stream.write('midi', fp='test_output.mid')


In [76]:
model = 0

In [79]:
# Load a previous model (dependency)
if model == 0:
    model = load_model("weights2-improvement-10-6.6137-bigger.hdf5")
generate(model)

In Generate
In Prepare Sequences Prediction
lengthToInt: {'0.0': 0, '0.25': 1, '0.3333333333333333': 2, '0.5': 3, '0.6666666666666666': 4, '0.75': 5, '1.0': 6, '1.25': 7, '1.3333333333333333': 8, '1.5': 9, '1.6666666666666667': 10, '1.75': 11, '10.0': 12, '16.0': 13, '18.0': 14, '2.0': 15, '2.25': 16, '2.5': 17, '2.75': 18, '20.0': 19, '3.0': 20, '3.25': 21, '3.5': 22, '4.0': 23, '4.25': 24, '4.5': 25, '5.0': 26, '5.5': 27, '6.0': 28, '6.25': 29, '6.5': 30, '7.0': 31, '8.0': 32, '8.5': 33, '9.5': 34}
din shape:
(22362, 16, 2)
din:
[[[0.60759494 0.08571429]
  [0.67088608 0.08571429]
  [0.7721519  0.08571429]
  ...
  [0.7721519  0.02857143]
  [0.87341772 0.02857143]
  [0.97468354 0.08571429]]

 [[0.67088608 0.08571429]
  [0.7721519  0.08571429]
  [0.87341772 0.14285714]
  ...
  [0.87341772 0.02857143]
  [0.97468354 0.08571429]
  [0.7721519  0.02857143]]

 [[0.7721519  0.08571429]
  [0.87341772 0.14285714]
  [0.97468354 0.        ]
  ...
  [0.97468354 0.08571429]
  [0.7721519  0.02857143]

114
prediction: [9.5367432e-07 1.6987324e-06 3.2782555e-07 2.3841858e-06 2.1159649e-06
 3.8743019e-07 2.8908253e-06 7.1525574e-07 2.6822090e-07 7.7486038e-07
 3.8743019e-07 1.4901161e-07 1.8179417e-06 2.6822090e-07 3.2782555e-07
 2.3841858e-07 9.2387199e-07 2.3841858e-07 1.2814999e-06 2.2351742e-06
 2.4139881e-06 3.8743019e-07 4.4703484e-07 9.2387199e-07 4.1723251e-07
 4.0531158e-06 1.7881393e-07 1.2814999e-06 1.8775463e-06 2.3841858e-07
 9.2235208e-04 4.1358173e-03 4.3095052e-03 8.3416700e-04 1.1734068e-03
 4.5817494e-03 6.6679120e-03 7.1400404e-04 1.8044710e-03 5.0635040e-03
 7.4848831e-03 2.5340915e-04 4.6044588e-05 2.9151738e-03 4.0529668e-03
 8.8116229e-03 6.4969063e-06 2.4171174e-03 3.2867789e-03 6.0912669e-03
 3.1203032e-05 3.7550926e-05 2.4062991e-03 3.9748549e-03 5.4116249e-03
 1.5932322e-04 3.9712787e-03 5.2419901e-03 6.5290928e-03 1.4662743e-04
 3.5006702e-03 4.7665536e-03 5.9162676e-03 4.6342611e-04 4.8898757e-03
 6.6321194e-03 3.3272505e-03 1.8304586e-04 3.7949085e-03 5.54

114
prediction: [9.2387199e-07 1.5795231e-06 2.6822090e-07 2.1755695e-06 1.8179417e-06
 4.1723251e-07 3.0398369e-06 8.0466270e-07 2.0861626e-07 7.7486038e-07
 2.6822090e-07 1.1920929e-07 1.8179417e-06 2.9802322e-07 2.3841858e-07
 1.4901161e-07 1.0728836e-06 2.0861626e-07 1.1920929e-06 2.5033951e-06
 1.9073486e-06 3.2782555e-07 4.1723251e-07 7.7486038e-07 4.7683716e-07
 2.5629997e-06 1.4901161e-07 1.1026859e-06 1.7583370e-06 2.0861626e-07
 7.5912476e-04 3.3595562e-03 3.5454035e-03 8.1717968e-04 1.1878908e-03
 4.8904717e-03 6.7656636e-03 7.6884031e-04 1.4802217e-03 4.3469071e-03
 6.3831210e-03 2.3260713e-04 4.4763088e-05 2.8021932e-03 3.9245188e-03
 8.5406005e-03 6.4671040e-06 2.4844706e-03 3.1222403e-03 6.0352087e-03
 3.5166740e-05 3.8892031e-05 2.3310483e-03 3.5972893e-03 4.9161017e-03
 1.7827749e-04 4.5616329e-03 5.8836043e-03 7.4418783e-03 1.4537573e-04
 3.1693280e-03 4.4790804e-03 5.6968927e-03 4.2423606e-04 4.4647455e-03
 6.2113702e-03 3.3528209e-03 1.9225478e-04 4.3861568e-03 6.24

114
prediction: [1.0430813e-06 2.0265579e-06 4.1723251e-07 2.5928020e-06 2.3841858e-06
 5.3644180e-07 3.4570694e-06 9.2387199e-07 2.9802322e-07 8.6426735e-07
 4.7683716e-07 1.7881393e-07 1.9073486e-06 3.5762787e-07 4.1723251e-07
 1.7881393e-07 1.1026859e-06 2.6822090e-07 1.4007092e-06 2.6524067e-06
 2.5331974e-06 4.4703484e-07 5.6624413e-07 9.5367432e-07 4.7683716e-07
 4.5001507e-06 2.3841858e-07 1.4603138e-06 2.1755695e-06 2.9802322e-07
 9.3254447e-04 4.1617751e-03 4.4051707e-03 8.6441636e-04 1.2982488e-03
 4.7863424e-03 7.2786808e-03 7.6884031e-04 1.8356144e-03 5.2970946e-03
 7.7167451e-03 2.6908517e-04 5.1945448e-05 3.1177998e-03 4.3235719e-03
 9.5265508e-03 7.4207783e-06 2.5286973e-03 3.3045709e-03 6.1640143e-03
 3.5405159e-05 3.9041042e-05 2.4688244e-03 4.0598810e-03 5.2397847e-03
 1.8748641e-04 4.4439435e-03 5.9889257e-03 7.4155331e-03 1.5461445e-04
 3.5948455e-03 5.0163865e-03 5.8407485e-03 5.2720308e-04 5.3231418e-03
 7.3382556e-03 3.4780502e-03 2.0131469e-04 4.0976703e-03 6.13

114
prediction: [1.1622906e-06 2.0563602e-06 4.4703484e-07 2.7120113e-06 2.5928020e-06
 5.3644180e-07 3.0994415e-06 8.3446503e-07 3.5762787e-07 7.7486038e-07
 5.6624413e-07 1.4901161e-07 1.9371510e-06 2.6822090e-07 3.8743019e-07
 2.9802322e-07 9.5367432e-07 2.6822090e-07 1.4007092e-06 2.3543835e-06
 2.8908253e-06 4.7683716e-07 6.2584877e-07 1.1026859e-06 5.3644180e-07
 6.1988831e-06 2.0861626e-07 1.6093254e-06 2.1457672e-06 2.3841858e-07
 1.0797381e-03 4.8824847e-03 5.0627887e-03 8.6465478e-04 1.2389123e-03
 4.5164526e-03 6.9338977e-03 7.0527196e-04 2.1255910e-03 5.8594346e-03
 8.6510777e-03 2.7889013e-04 5.1409006e-05 3.1570196e-03 4.3601394e-03
 9.5009804e-03 6.9737434e-06 2.4260879e-03 3.4359396e-03 6.1940849e-03
 3.0398369e-05 3.7163496e-05 2.4929643e-03 4.3374002e-03 5.7216883e-03
 1.6087294e-04 3.8226843e-03 5.1794350e-03 6.3366294e-03 1.5306473e-04
 3.8520992e-03 5.1693618e-03 6.0762167e-03 5.3712726e-04 5.5017769e-03
 7.3985457e-03 3.4140348e-03 1.8656254e-04 3.5692453e-03 5.37

...

114
prediction: [1.0132790e-06 1.6987324e-06 3.8743019e-07 2.3245811e-06 2.0563602e-06
 4.1723251e-07 2.8610229e-06 7.1525574e-07 2.6822090e-07 6.5565109e-07
 4.1723251e-07 1.4901161e-07 1.8179417e-06 2.6822090e-07 3.5762787e-07
 2.3841858e-07 9.8347664e-07 1.7881393e-07 1.2814999e-06 2.2053719e-06
 2.3841858e-06 4.1723251e-07 4.7683716e-07 9.2387199e-07 4.1723251e-07
 3.9935112e-06 2.3841858e-07 1.2516975e-06 1.8179417e-06 2.0861626e-07
 9.1242790e-04 4.0992498e-03 4.2984784e-03 8.3324313e-04 1.1653304e-03
 4.5690238e-03 6.6754520e-03 7.0998073e-04 1.7857254e-03 5.0194860e-03
 7.4336827e-03 2.5275350e-04 4.5686960e-05 2.8930008e-03 4.0310919e-03
 8.7792575e-03 6.5267086e-06 2.4069250e-03 3.2652318e-03 6.0528517e-03
 3.1381845e-05 3.7342310e-05 2.3969412e-03 3.9573908e-03 5.3558350e-03
 1.6036630e-04 3.9812326e-03 5.2595139e-03 6.5631270e-03 1.4600158e-04
 3.4928918e-03 4.7531724e-03 5.8943629e-03 4.6133995e-04 4.8750341e-03
 6.6312551e-03 3.3158064e-03 1.8283725e-04 3.7954152e-03 5.55

array predPitch: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0]
array predLength: [0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
result ['D5' '0.5']
pattern: [[0.55696203 0.08571429]
 [0.40506329 0.08571429]
 [0.37974684 0.08571429]
 [0.94936709 0.08571429]
 [0.75949367 0.08571429]
 [0.5443038  0.08571429]
 [0.7721519  0.17142857]
 [0.73417722 0.02857143]
 [0.6835443  0.08571429]
 [0.65822785 0.02857143]
 [0.56962025 0.02857143]
 [0.75949367 0.08571429]
 [0.73417722 0.02857143]
 [0.70886076 0.08571429]
 [0.78481013 0.08571429]
 [0.72151899 0.02857143]
 [0.6835443  0.08571429]]
prediction_input:
[[[0.40506329 0.08571429]
  [0.37974684 0.08571429]
  [0.94936709 0.08571429]
  [0.75949367 0.08571429]
  [0.5443038  0.08571429]
  [0.7721519  0.17142857]
  [0.73417722 0.02857143]
  [0.6835443  0.08571429]
  [0.65822785 0.02857143]
  [0.56962025 0.02857143

114
prediction: [1.0132790e-06 1.4901161e-06 3.5762787e-07 2.3245811e-06 1.9967556e-06
 4.1723251e-07 2.8312206e-06 6.5565109e-07 2.3841858e-07 7.1525574e-07
 3.2782555e-07 1.4901161e-07 1.8775463e-06 2.0861626e-07 3.2782555e-07
 2.0861626e-07 9.2387199e-07 2.0861626e-07 1.1622906e-06 2.1755695e-06
 2.1755695e-06 3.8743019e-07 4.4703484e-07 9.2387199e-07 4.7683716e-07
 3.4272671e-06 1.1920929e-07 1.1920929e-06 1.7583370e-06 1.4901161e-07
 8.6972117e-04 3.8731992e-03 4.0404797e-03 8.3231926e-04 1.1326075e-03
 4.6343505e-03 6.4965785e-03 7.1617961e-04 1.6931295e-03 4.7508776e-03
 7.0661306e-03 2.4431944e-04 4.4107437e-05 2.8088689e-03 3.9275885e-03
 8.4581375e-03 6.3180923e-06 2.4158657e-03 3.2643974e-03 6.1092675e-03
 3.1709671e-05 3.8444996e-05 2.3861825e-03 3.8630664e-03 5.3901970e-03
 1.5625358e-04 4.0013790e-03 5.1914155e-03 6.5334439e-03 1.4626980e-04
 3.3805072e-03 4.5952797e-03 5.9619248e-03 4.2974949e-04 4.5858920e-03
 6.2545538e-03 3.3102632e-03 1.8274784e-04 3.8980246e-03 5.58

[array(['B3', '0.5'], dtype='<U3'), array(['A5', '0.5'], dtype='<U3'), array(['E5', '0.25'], dtype='<U4'), array(['G3', '0.25'], dtype='<U4'), array(['F3', '1.0'], dtype='<U3'), array(['D5', '0.5'], dtype='<U3'), array(['E5', '0.5'], dtype='<U3'), array(['B5', '0.5'], dtype='<U3'), array(['A4', '0.5'], dtype='<U3'), array(['A4', '0.5'], dtype='<U3'), array(['E5', '0.25'], dtype='<U4'), array(['E5', '0.25'], dtype='<U4'), array(['C5', '1.0'], dtype='<U3'), array(['E4', '0.5'], dtype='<U3'), array(['F3', '0.5'], dtype='<U3'), array(['D5', '0.5'], dtype='<U3'), array(['D5', '0.5'], dtype='<U3'), array(['F5', '0.5'], dtype='<U3'), array(['E3', '0.5'], dtype='<U3'), array(['G5', '0.5'], dtype='<U3'), array(['D5', '0.5'], dtype='<U3'), array(['B5', '0.25'], dtype='<U4'), array(['E3', '0.5'], dtype='<U3'), array(['C5', '0.5'], dtype='<U3'), array(['E5', '0.5'], dtype='<U3'), array(['B5', '0.5'], dtype='<U3'), array(['E3', '0.5'], dtype='<U3'), array(['C5', '2.0'], dtype='<U3'), array(['F5', '

NameError: name 'patter' is not defined

In [120]:
generate(model)

In Generate
In Prepare Sequences Prediction
din shape:
(736, 4, 2)
din:
[[[0.46511628 0.2       ]
  [0.55813953 0.2       ]
  [0.65116279 0.2       ]
  [0.81395349 0.33333333]]

 [[0.55813953 0.2       ]
  [0.65116279 0.2       ]
  [0.81395349 0.33333333]
  [0.95348837 0.        ]]

 [[0.65116279 0.2       ]
  [0.81395349 0.33333333]
  [0.95348837 0.        ]
  [0.81395349 0.        ]]

 ...

 [[0.97674419 0.06666667]
  [0.1627907  0.26666667]
  [0.8372093  0.06666667]
  [0.58139535 0.2       ]]

 [[0.1627907  0.26666667]
  [0.8372093  0.06666667]
  [0.58139535 0.2       ]
  [0.34883721 0.06666667]]

 [[0.8372093  0.06666667]
  [0.58139535 0.2       ]
  [0.34883721 0.06666667]
  [0.51162791 0.8       ]]]
pattern [[0.81395349 0.2       ]
 [0.93023256 0.2       ]
 [0.3255814  0.06666667]
 [0.48837209 0.06666667]]
seqLength: 4
npitches 43 nlengths 15
In genNotes(): noteIn[start] = [[0.81395349 0.2       ]
 [0.93023256 0.2       ]
 [0.3255814  0.06666667]
 [0.48837209 0.06666667]]
inputSiz

array predPitch: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0
 0 0 0 0 0 0]
array predLength: [0 1 0 0 0 0 0 0 0 0 0 0 0 0 0]
result ['E4' '0.25']
pattern: [[0.46511628 0.06666667]
 [0.1627907  0.06666667]
 [0.65116279 0.06666667]
 [0.65116279 0.06666667]
 [0.65116279 0.06666667]]
prediction_input:
[[[0.1627907  0.06666667]
  [0.65116279 0.06666667]
  [0.65116279 0.06666667]
  [0.65116279 0.06666667]]]
58
prediction: [1.3251936e-03 2.1538190e-03 5.1055933e-05 1.7906200e-04 8.8226428e-04
 3.4546161e-03 2.6842657e-02 4.5336869e-02 8.1832928e-05 1.9438720e-04
 1.3683978e-03 1.6145708e-06 5.1306945e-04 4.6745094e-04 1.6554907e-03
 7.6005897e-05 1.3865913e-04 9.5951307e-04 6.2552508e-04 3.2841126e-04
 1.5616295e-02 4.3502485e-05 9.5697294e-05 1.4534686e-03 1.5431615e-03
 3.8331104e-03 9.5899159e-06 1.7825412e-02 8.5581884e-02 8.0381846e-03
 2.2820859e-04 9.5483717e-03 3.1843994e-04 2.0952216e-04 5.6019928e-02
 4.0731090e-04 1.2289716e-03 1.1946738e-03 3.3633431

 2.6869481e-02 2.1784890e-03 2.8165770e-04]
prediction length: 58
Before
[6.21047278e-04 7.19270683e-05 4.09530713e-07 4.76518726e-05
 4.86126228e-05 3.67396278e-03 5.27618174e-03 8.64670515e-01
 6.31222383e-06 7.36781067e-06 1.78260671e-05 1.31682043e-09
 2.11113971e-07 1.16863892e-04 2.64729606e-05 8.64072717e-07
 1.73527076e-06 8.61212320e-05 8.49237767e-05 1.38652496e-07
 8.32182064e-04 3.03838902e-07 1.92331368e-06 1.57358823e-04
 2.11617822e-04 2.23461047e-05 3.36125623e-07 1.92187377e-03
 6.36028275e-02 9.87121166e-05 4.40869781e-06 2.45235744e-04
 3.34939102e-07 7.75293574e-06 1.24841193e-02 1.89148250e-05
 1.25318256e-05 8.14203406e-04 6.16370244e-08 4.18558957e-05
 1.34914008e-05 4.25526341e-05 4.51737928e-04]
[2.30394676e-03 1.06348572e-02 4.53014945e-04 1.13551207e-04
 1.19800898e-04 8.43021510e-08 1.09362236e-06 1.93097425e-04
 8.00864364e-04 1.93490692e-07 1.65950773e-08 3.03686102e-04
 2.68694814e-02 2.17848900e-03 2.81657703e-04]
sumNote 0.955746 sumLength 0.044254
Afte

array predPitch: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0
 0 0 0 0 0 0]
array predLength: [0 1 0 0 0 0 0 0 0 0 0 0 0 0 0]
result ['F3' '0.25']
pattern: [[0.65116279 0.06666667]
 [0.65116279 0.06666667]
 [0.72093023 0.86666667]
 [0.65116279 0.        ]
 [0.79069767 0.06666667]]
prediction_input:
[[[0.65116279 0.06666667]
  [0.72093023 0.86666667]
  [0.65116279 0.        ]
  [0.79069767 0.06666667]]]
58
prediction: [3.6506806e-04 2.7107078e-05 1.8324984e-06 1.7587899e-05 2.3528544e-05
 6.2302956e-03 9.1964200e-02 2.7922392e-03 4.2759082e-05 6.1904120e-06
 3.2614867e-04 7.7278196e-07 2.5377469e-05 2.1630526e-03 1.7213186e-03
 1.5879086e-05 4.1075559e-06 2.0574410e-03 3.7283417e-06 6.2127714e-05
 6.3954657e-03 5.4133643e-04 2.1485428e-05 3.5166193e-03 4.6285498e-03
 4.9684162e-04 4.9681526e-06 9.8909962e-04 4.4865049e-02 2.5315583e-02
 4.2705311e-04 1.4786702e-03 7.3393035e-06 8.1131649e-05 8.4084898e-02
 1.2719557e-03 5.5640354e-04 5.9832650e-04 1.6856251

58
prediction: [8.1394194e-04 2.7422693e-03 1.5687030e-04 2.1196797e-04 1.4467083e-03
 4.7671655e-03 1.8164331e-02 1.7818872e-02 1.5538953e-04 1.7800892e-04
 1.3744901e-03 1.7943252e-05 1.0063621e-03 1.7490137e-03 3.4545548e-03
 2.3102992e-04 4.8853375e-04 1.2276807e-03 3.1725955e-04 5.3413759e-04
 1.3176120e-02 1.7715689e-04 1.3434447e-04 1.8996557e-03 3.6607883e-03
 4.2502978e-03 6.3119180e-05 1.5023080e-02 3.9798398e-02 6.0887849e-03
 1.5662469e-04 1.6404817e-02 3.9129279e-04 1.6833516e-04 5.4639779e-02
 4.2017861e-04 2.0664912e-03 8.9486100e-04 2.0372382e-04 1.6111501e-04
 1.5664898e-02 1.4752984e-02 3.3800784e-03 1.4979863e-02 6.4210463e-01
 1.9515961e-02 1.6516501e-03 5.6746706e-02 1.3016198e-04 1.0647295e-04
 5.1385612e-04 1.1039268e-03 1.3012181e-05 1.8943982e-04 5.6069432e-04
 8.1670219e-03 1.1419101e-03 2.6413649e-03]
prediction length: 58
Before
[8.13941937e-04 2.74226931e-03 1.56870301e-04 2.11967970e-04
 1.44670834e-03 4.76716552e-03 1.81643311e-02 1.78188719e-02
 1.553895

58
prediction: [1.41703920e-03 1.75625889e-03 8.31700308e-05 2.15652399e-04
 9.70804715e-04 5.10471361e-03 3.56805734e-02 3.70201170e-02
 1.48023886e-04 2.88640847e-04 8.78648832e-04 4.06960316e-06
 5.92297176e-04 1.42509746e-03 2.54247175e-03 1.30471133e-04
 2.22893083e-04 1.41407805e-03 4.00043180e-04 3.35285877e-04
 1.64308660e-02 9.20548628e-05 7.03151309e-05 3.24474857e-03
 4.69011068e-03 3.06628877e-03 1.91050240e-05 1.78527534e-02
 7.75273293e-02 5.49756829e-03 2.01524541e-04 1.77358873e-02
 2.88713258e-04 2.40948910e-04 9.12831649e-02 4.22351353e-04
 1.49399636e-03 1.54228555e-03 1.03939645e-04 1.99022907e-04
 5.48639102e-03 7.10111670e-03 2.36863643e-03 1.47882244e-02
 5.58867395e-01 1.63490642e-02 2.35489593e-03 3.28213796e-02
 4.88293044e-05 5.59415494e-05 4.99892805e-04 2.91884970e-03
 9.41962298e-06 5.81490422e-05 6.08372444e-04 1.64997801e-02
 4.17318987e-03 2.35712598e-03]
prediction length: 58
Before
[1.41703920e-03 1.75625889e-03 8.31700308e-05 2.15652399e-04
 9.708047